In [16]:
import os
import math
import pandas as pd

def calculate_h_index(quotation): #h_ndex
    quotation.sort(reverse=True)  # 논문을 내림차순으로 정렬

    h_index = 0
    for i, quotation in enumerate(quotation):
        if quotation >= i + 1:
            h_index = i + 1
        else:
            break

    return h_index

def calculate_i10_index(quotation):  #i10_index
    i10_index = sum(1 for quotation in quotation if quotation >= 10)
    return i10_index

def calculate_g_index(quotation):  #g_index
    quotation.sort(reverse=True)  # 논문을 내림차순으로 정렬

    g_index = 0
    quotation_sum=0
    for i, quotation in enumerate(quotation):
        quotation_sum+=quotation
        if quotation_sum >= (i + 1)**2:
            g_index = i + 1

    return g_index

#Object 타입에서 숫자형 체크용
def is_numeric(value):
    try:
        float(value)  # float으로 변환 가능한 경우 숫자
        return True
    except (ValueError, TypeError):
        return False

def recentness(pYears):
    # dt = datetime.datetime.now()#현재날짜
    dt = 2013
    rct = 0
    lct = 0
    if len(pYears) == 0:
        rct = 0
        lct = 0
    else:
        year_avg = sum(pYears) / len(pYears)
        if year_avg >= int(dt)-2: #int(dt.year)-2:
            lct = 1
        else:
            lct = max(round((1-(int(dt)-3-year_avg)*0.1),2), 0)
        # elif int(dt)-15 < year_avg <= int(dt)-3:
        #     lct = max(round((1-(int(dt)-3-year_avg)*0.1),2), 0)

        rct += len(pYears) #연도 개수

    return rct, lct

pd.set_option('display.max_columns', None)
pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_rows', None)

In [17]:
#authors.all 파일 위치 주소
authors_file_path = r"C:\Users\isjun\바탕 화면\연구실\전문가 검색\gsc_data\gsc_data\authors.all"

try:
    with open(authors_file_path, 'r', encoding='cp1252') as file:
        lines = file.read().splitlines()
        data = [line.split('|') for line in lines]
        columns = ["Valid", "Name", "Affiliation", "Email Domain", "Citation Count", "ID"]
        df_a = pd.DataFrame(data,columns=columns) # authors 의 a
        # df_a = df_a.drop(columns=["C6", "C7"])
        print("변환 완료")
except FileNotFoundError:
    print("파일을 찾을 수 없습니다.")
except UnicodeDecodeError:
    print("파일을 ANSI(Windows-1252) 인코딩으로 열 수 없습니다.")
    
df_a_copy = df_a.copy()  # df_a의 복사본 생성


for index, row in df_a_copy.iterrows():
    if pd.isna(row[5]):  
        if pd.isna(row[4]):
            if pd.isna(row[3]):  # 1의 경우
                row[5] = row[2] 
            else:  # 2,3,4 의 경우
                row[5] = row[3]
                if is_numeric(row[2]): # 4의 경우
                    row[4] = row[2]
                    row[2] = None
                    row[3] = None
                elif '.' in str(row[2]):  # 3의 경우
                    row[3] = row[2]
                    row[2] = None
                    row[4] = None
                else: # 2의 경우
                    row[3] = None
        else:  # 5,6,7 의 경우
            row[5] = row[4] 
            if is_numeric(row[3]): # 6,7 의 경우
                row[4] = row[3]
                if '.' in str(row[2]): # 7 의 경우
                    row[3] = row[2]
                    row[2] = None
                else: # 6의 경우
                    
                    row[3] = None
            else: #5의 경우
                row[4] = None

변환 완료


C:\Users\isjun\AppData\Local\Temp\ipykernel_34316\303757249.py:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if pd.isna(row[5]):
C:\Users\isjun\AppData\Local\Temp\ipykernel_34316\303757249.py:22: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if pd.isna(row[4]):
C:\Users\isjun\AppData\Local\Temp\ipykernel_34316\303757249.py:23: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if pd.isna(row[3]):  # 1의 경우
C:\Users\isjun\AppData\Local

In [18]:
Author_df=df_a_copy.drop(columns=['Valid', 'Affiliation', 'Email Domain'])
     
print(Author_df)

                                                    Name Citation Count            ID
0                                            Rock Ouimet           1167  LrG_vOwAAAAJ
1                                  Mohammad Kalami Yazdi             65  9Ouxj1gAAAAJ
2                                          Jiuguang Wang             51  3UxwoGYAAAAJ
3                                         Heleen Slagter           1442  FctSSDoAAAAJ
4                                         Keith W Slater             48  tRPUC6AAAAAJ
5                                       Melanie Langford            136  gfqq5S4AAAAJ
6                                        Ghislain Bidaut            116  rsyLTo8AAAAJ
7                                       Kush R. Varshney            128  hMZMhLoAAAAJ
8                                    Patrick Schultheiss             27  a8pfjUAAAAAJ
9                                       Michael H Tatham           1352  a1RXF1sAAAAJ
10                                           Aki Vehta

In [27]:
#gsc_data\DATA 폴더 경로
folder_path = r"C:\Users\isjun\바탕 화면\연구실\전문가 검색\gsc_data\gsc_data\DATA"

id_year_cit={}
id_year_cit_df=[]
# df_a_copy의 각 행에서 1번 열의 값을 추출
for index, row in df_a_copy.iterrows():
    name = row.iloc[5]  # 1번 열의 값

    converted_list=[]
    citations = [] #인용수
    years = [] #연도

    # 파일 경로 생성
    file_path = os.path.join(folder_path, name + "_.dat")
   
    # 파일이 존재하는지 확인
    if os.path.exists(file_path):
        with open(file_path, 'r', encoding='utf-8') as file:
            # 파일의 각 줄을 읽어 리스트로 저장
            lines = file.readlines()
 
        # 각 줄을 나누어서 리스트로 저장
        cit_year_list = [line.strip().split('|') for line in lines]

        citations = [] #인용수
        years = [] #연도

        for line_list in cit_year_list:
            citations.append(int(line_list[0]))
            years.append(int(line_list[1]))

        year_count = {} #각 연도 별 논문 수

        for year in years:
            if year in year_count:
                year_count[year] += 1
            else:
                year_count[year] = 1

        sorted_year_count = dict(sorted(year_count.items()))
        frequency_list = list(sorted_year_count.values())

        year_cit_df = pd.DataFrame({'Year': years,'citation': citations})

        grouped_df = year_cit_df.groupby('Year', as_index=False)['citation'].sum()
        grouped_df['Paper_Count']=frequency_list
        # converted_list = grouped_df.values.tolist()

    else:
        print(f"파일을 찾을 수 없습니다: {file_path}")

    id_year_cit[name]={'year_citation': grouped_df}


    grouped_df_copy = grouped_df.copy()
    grouped_df_copy['ID']=name
    id_year_cit_df.append(grouped_df_copy)

In [35]:
merged_df = pd.concat(id_year_cit_df, ignore_index=True)
merged_df['Year'] = merged_df['Year'].astype(int)
merged_df['citation'] = merged_df['citation'].astype(int)
merged_df['Paper_Count'] = merged_df['Paper_Count'].astype(int)

new_order = ['ID', 'Year', 'Paper_Count', 'citation']
merged_df = merged_df[new_order]

In [ ]:
merged_df.to_csv(f"C:/Users/isjun/바탕 화면/연구실/전문가 검색/year_citation_papercnt_all/year_citation_papercnt.csv", index=False)

In [23]:
for index, row in df_a_copy.iterrows():
    name = row.iloc[5]  # 1번 열의 값
    id_year_cit[name]['year_citation'].to_csv(f"C:/Users/isjun/바탕 화면/연구실/전문가 검색/year_citation_papercnt/{name}.csv", index=False)

In [ ]:
print(id_year_cit['LrG_vOwAAAAJ']['year_citation'])

In [ ]:
import matplotlib.pyplot as plt
 
plt.plot(id_year_cit['M5_mEHQAAAAJ']['year_citation']['Year'], id_year_cit['M5_mEHQAAAAJ']['year_citation']['citation'])
plt.show()